# core

> Basic building blocks

In [ ]:
#|default_exp core

In [ ]:
#|hide
from nbdev.showdoc import *

In [ ]:
#|export
import io
import numpy as np
import pandas as pd
from fastcore.all import *
import scipy.io.wavfile as wav
from IPython.display import Audio
from itertools import combinations
from collections import defaultdict
from mingus.core import chords as mingus_chords, notes as mingus_notes

# Base Variables

These variables contain the basic orderings for Western music theory.

In [ ]:
#|export
BASE_NOTES = ["C", "D", "E", "F", "G", "A", "B"]
CHROMATIC_NOTES = ["C", "C#", "D", "D#", "E", "F", "F#", "G", "G#", "A", "A#", "B"]
INTERVALS = ["1", "b2", "2", "b3", "3", "4", "#4", "5", "b6", "6", "b7", "7"]
NOTE_MAPPING = {
    "C": 0,
    "C#": 1,
    "Db": 1,
    "D": 2,
    "D#": 3,
    "Eb": 3,
    "E": 4,
    "Fb": 4,
    "E#": 5,
    "F": 5,
    "F#": 6,
    "Gb": 6,
    "G": 7,
    "G#": 8,
    "Ab": 8,
    "A": 9,
    "A#": 10,
    "Bb": 10,
    "B": 11,
    "Cb": 11,
    "B#": 0
}
INTERVAL_NAMES = {
    "1": "unison",
    "b2": "minor second",
    "2": "major second",
    "#2": "augmented second",
    "b3": "minor third",
    "3": "major third",
    "b4": "minor fourth",
    "4": "perfect fourth",
    "#4": "augmented fourth",
    "b5": "diminished fifth",
    "5": "perfect fifth",
    "#5": "augmented fifth",
    "b6": "minor sixth",
    "6": "major sixth",
    "#6": "augmented sixth",
    "b7": "minor seventh",
    "7": "major seventh",
    "8": "octave",
    "b9": "minor ninth",
    "9": "major ninth",
    "#9": "augmented ninth",
    "b10": "minor tenth",
    "10": "major tenth",
    "b11": "minor eleventh",
    "11": "major eleventh",
    "#11": "augmented eleventh",
    "b12": "minor twelfth",
    "12": "major twelfth",
    "b13": "minor thirteenth",
    "13": "major thirteenth",
    "#13": "augmented thirteenth"
}
INTERVAL_HALF_STEPS = {
    "1": 0,
    "#1": 1,
    "b2": 1,
    "2": 2,
    "#2": 3,
    "b3": 3,
    "3": 4,
    "b4": 4,
    "4": 5,
    "#4": 6,
    "b5": 6,
    "5": 7,
    "#5": 8,
    "b6": 8,
    "6": 9,
    "#6": 10,
    "b7": 10,
    "7": 11,
    "8": 12,
    "b9": 13,
    "9": 14,
    "#9": 15,
    "10": 16,
    "11": 17,
    "#11": 18,
    "12": 19,
    "b13": 20,
    "13": 21,
    "#13": 22,
    "14": 23,
    "15": 24
}
STEPS_TO_INTERVAL = {
    0: "1",
    1: "b2",
    2: "2",
    3: "b3",
    4: "3",
    5: "4",
    6: "b5",
    7: "5",
    8: "b6",
    9: "6",
    10: "b7",
    11: "7",
}

STEPS_TO_INTERVAL_FULL = {
    0: "unison",
    1: "minor second",
    2: "major second",
    3: "minor third",
    4: "major third",
    5: "perfect fourth",
    6: "tritone",
    7: "perfect fifth",
    8: "minor sixth",
    9: "major sixth",
    10: "minor seventh",
    11: "major seventh",
}
INTERVAL_TYPES = {
    0: "Perfect Consonant", # Unison
    1: "Sharp Dissonant", # Minor Second
    2: "Mild Dissonant", # Major Second
    3: "Soft Consonant", # Minor Third
    4: "Soft Consonant", # Major Third
    5: "Contextual", # Perfect Fourth
    6: "Neutral", # Tritone/Augmented Fourth/Diminished Fifth
    7: "Perfect Consonant", # Perfect Fifth
    8: "Soft Consonant", # Minor Sixth
    9: "Soft Consonant", # Major Sixth
    10: "Mild Dissonant", # Minor Seventh
    11: "Sharp Dissonant", # Major Seventh
}

SCALES = {# Major modes
          "ionian": ["1", "2", "3", "4", "5", "6", "7"],
          "major": ["1", "2", "3", "4", "5", "6", "7"],
          "minor": ["1", "2", "b3", "4", "5", "b6", "b7"],
          "natural minor": ["1", "2", "b3", "4", "5", "b6", "b7"],
          "dorian": ["1", "2", "b3", "4", "5", "6", "b7"],
          "phrygian": ["1", "b2", "b3", "4", "5", "b6", "b7"],
          "lydian": ["1", "2", "3", "#4", "5", "6", "7"],
          "mixolydian": ["1", "2", "3", "4", "5", "6", "b7"],
          "aeolian": ["1", "2", "b3", "4", "5", "b6", "b7"],
          "locrian": ["1", "b2", "b3", "4", "b5", "b6", "b7"],
          # Melodic Minor modes
          "melodic minor": ["1", "2", "b3", "4", "5", "6", "7"],
          "dorian b2": ["1", "b2", "b3", "4", "5", "6", "b7"],
          "lydian augmented": ["1", "2", "3", "#4", "#5", "6", "7"],
          "lydian b7": ["1", "2", "3", "#4", "5", "6", "b7"],
          "lydian dominant": ["1", "2", "3", "#4", "5", "6", "b7"],
          "acoustic": ["1", "2", "3", "#4", "5", "6", "b7"],
          "mixolydian #11": ["1", "2", "3", "#4", "5", "6", "b7"],
          "locrian n2": ["1", "2", "b3", "4", "b5", "b6", "7"],
          "altered": ["1", "b2", "b3", "b4", "b5", "b6", "b7"],
          "altered dominant": ["1", "b2", "b3", "b4", "b5", "b6", "b7"],
          "diminished whole-tone": ["1", "b2", "b3", "b4", "b5", "b6", "b7"],
          "dominant whole-tone": ["1", "b2", "b3", "b4", "b5", "b6", "b7"],
          "aeolian dominant": ["1", "2", "3", "4", "5", "b6", "b7"],
          # Harmonic minor modes
          "harmonic minor": ["1", "2", "b3", "4", "5", "b6", "7"],
          "locrian 6": ["1", "b2", "b3", "4", "b5", "6", "b7"],
          "ionian augmented": ["1", "2", "3", "4", "#5", "6", "7"],
          "dorian #4": ["1", "2", "b3", "#4", "5", "6", "b7"],
          "phrygian major": ["1", "b2", "3", "4", "5", "b6", "b7"],
          "phrygian dominant": ["1", "b2", "3", "4", "5", "b6", "b7"],
          "spanish phrygian": ["1", "b2", "3", "4", "5", "b6", "b7"],
          "spanish major": ["1", "b2", "3", "4", "5", "b6", "b7"],
          "spanish": ["1", "b2", "3", "4", "5", "b6", "b7"],
          "lydian #2": ["1", "#2", "3", "#4", "5", "6", "7"],
          "lydian #9": ["1", "#2", "3", "#4", "5", "6", "7"],
          "altered dominant bb7": ["1", "b2", "b3", "b4", "b5", "b6", "6"],
          "altered 13": ["1", "b2", "b3", "b4", "b5", "b6", "6"],
          # Harmonic major modes
          "harmonic major": ["1", "2", "3", "4", "5", "b6", "7"],
          "ionian b6": ["1", "2", "3", "4", "5", "b6", "7"],
          "dorian b5": ["1", "2", "b3", "4", "b5", "6", "b7"],
          "phrygian b4": ["1", "b2", "b3", "b4", "5", "b6", "b7"],
          "lydian b3": ["1", "2", "b3", "#4", "5", "6", "7"],
          "melodic minor #4": ["1", "2", "b3", "#4", "5", "6", "7"],
          "mixolydian b2": ["1", "b2", "3", "4", "5", "6", "b7"],
          # Lydian augmented already defined in melodic minor modes
          "locrian bb7": ["1", "b2", "b3", "4", "b5", "b6", "6"],
          # Double harmonic major modes
          "double harmonic major": ["1", "b2", "3", "4", "5", "b6", "7"],
          "double harmonic": ["1", "b2", "3", "4", "5", "b6", "7"],
          "lydian #2#6": ["1", "#2", "3", "#4", "5", "#6", "7"],
          "ultraphrygian": ["1", "b2", "b3", "b4", "5", "b6", "6"],
          "hungarian minor": ["1", "2", "b3", "#4", "5", "b6", "7"],
          "oriental": ["1", "b2", "3", "4", "b5", "6", "b7"], # Mixolydian b2 with lowered 5
          "ionian aug#2": ["1", "#2", "3", "4", "#5", "6", "7"],
          "locrian bb3bb7": ["1", "b2", "2", "4", "b5", "b6", "6"],
          # Bebop scales
          "bebop dominant": ["1", "2", "3", "4", "5", "6", "#6", "7"],
          "bebop major": ["1", "2", "3", "4", "5", "b6", "6", "7"],
          "bebop blues": ["1", "2", "b3", "3", "4", "5", "6", "b7"],
          "bebop melodic minor": ["1", "2", "b3", "4", "5", "b6", "6", "7"],
          # Pentatonic scales
          "pentatonic major": ["1", "2", "3", "5", "6"],
          "major pentatonic": ["1", "2", "3", "5", "6"],
          "pentatonic minor": ["1", "b3", "4", "5", "b7"],
          "minor pentatonic": ["1", "b3", "4", "5", "b7"],
          "pentatonic blues": ["1", "b3", "4", "b5", "5", "b7"],
          "blues pentatonic": ["1", "b3", "4", "b5", "5", "b7"],
          "pentatonic neutral": ["1", "2", "4", "5", "b7"],
          "neutral pentatonic": ["1", "2", "4", "5", "b7"],
          "pentatonic rock": ["1", "b3", "4", "#5", "b7"],
          "rock pentatonic": ["1", "b3", "4", "#5", "b7"],
          "jue": ["1", "b3", "4", "#5", "b7"], # Same intervals as rock pentatonic
          "pentatonic scottish": ["1", "2", "4", "5", "6"],
          "scottish pentatonic": ["1", "2", "4", "5", "6"],
          # Blues scales
          "blues major": ["1", "2", "b3", "3", "5", "6"],
          "blues minor": ["1", "b3", "4", "b5", "5", "b7"],
          "blues": ["1", "b3", "4", "b5", "5", "b7"], # Shorthand for Blues Minor
          "blues diminished": ["1", "b2", "b3", "3", "b5", "5", "6", "b7"],
          "aux diminished blues": ["1", "b2", "b3", "3", "b5", "5", "6", "b7"], 
          "half-whole": ["1", "b2", "b3", "3", "b5", "5", "6", "b7"],
          "balinese": ["1", "b2", "b3", "3", "b5", "5", "6", "b7"], 
          # Gypsy scales
          "gypsy major": ["1", "b2", "3", "4", "5", "b6", "7"],
          "gypsy minor": ["1", "2", "b3", "b5", "5", "b6", "7"],
          "spanish gypsy": ["1", "b2", "3", "4", "5", "b6", "b7"], # Same as Phrygian dominant
          "hungarian gypsy": ["1", "2", "b3", "#4", "5", "b6", "b7"], # Hungarian minor with lowered 7
          # Diminished scales
          "diminished": ["1", "2", "b3", "4", "b5", "b6", "6", "7"],
          "tonic diminished": ["1", "2", "b3", "4", "b5", "b6", "6", "7"],
          "whole-half": ["1", "2", "b3", "4", "#4", "#5", "6", "7"],
          "dominant diminished": ["1", "b2", "b3", "3", "#4", "5", "6", "b7"],
          "whole": ["1", "2", "3", "#4", "#5", "#6"],
          "whole-tone": ["1", "2", "3", "#4", "#5", "#6"],
          "aux augmented": ["1", "2", "3", "#4", "#5", "#6"],
          # Maqam
          "bayati shuri": ["1", "2", "b3", "4", "b5", "6", "b7"],
          "hijaz": ["1", "b2", "3", "4", "5", "b6", "b7"],
          "hijaz kar": ["1", "b2", "3", "4", "5", "6", "7"],
          "huzam": ["1", "b2", "b3", "3", "5", "b6", "b7"],
          "nikriz": ["1", "2", "3", "#4", "5", "6", "7"],
          "tunisian": ["1", "2", "3", "#4", "5", "6", "7"],
          "saba": ["1", "2", "b3", "3", "5", "b6", "b7"],
          "sabah": ["1", "2", "b3", "3", "5", "b6", "b7"],
          "suznak": ["1", "2", "3", "4", "5", "#5", "7"],
          "neveseri": ["1", "b2", "b3", "3", "5", "b6", "b7", "7"],
          # Greek
          "pireaus": ["1", "b2", "3", "#4", "5", "#5", "7"],
          "tsinganikos": ["1", "b2", "3", "4", "#4", "6", "#6"],
          # Hindustani
          "marwa": ["1", "b2", "3", "#4", "5", "6", "7"],
          "poorvi": ["1", "b2", "3", "#4", "5", "6", "7"],
          "segah": ["1", "#2", "3", "4", "5", "#5", "7"],
          "todi": ["1", "b2", "b3", "#4", "5", "b6", "7"],
          # Carnatic
          "charukeshi": ["1", "2", "3", "4", "5", "b6", "b7"],
          "dharmaavati": ["1", "2", "b3", "b5", "5", "6", "7"],
          "lataangi": ["1", "2", "3", "#4", "5", "6", "7"],
          "vachaspati": ["1", "2", "3", "#4", "5", "6", "#6"],
          "natakpriya": ["1", "b2", "b3", "4", "5", "6", "b7"],
          "rampriya": ["1", "b2", "3", "#4", "5", "6", "#6"],
          "suryakant": ["1", "b2", "3", "4", "5", "6", "7"],
          # Japanese
          "joshi akikaze": ["1", "2", "b3", "5", "6"],
          "akikaze joshi": ["1", "2", "b3", "5", "6"],
          "joshi hira": ["1", "2", "b3", "5", "b6"],
          "hira joshi": ["1", "2", "b3", "5", "b6"],
          "joshi iwato": ["1", "b2", "4", "b5", "b7"],
          "iwato joshi": ["1", "b2", "4", "b5", "b7"],
          "joshi kokin": ["1", "2", "4", "5", "b6"],
          "kokin joshi": ["1", "2", "4", "5", "b6"],
          "joshi kumoi": ["1", "b2", "4", "5", "b6"],
          "kumoi joshi": ["1", "b2", "4", "5", "b6"],
          "joshi okinawa": ["1", "3", "4", "5", "7"],
          "okinawa joshi": ["1", "3", "4", "5", "7"],
          "sen in": ["1", "b2", "4", "5", "b7"],
          "in sen": ["1", "b2", "4", "5", "b7"],
          # Misc.
          "chromatic": ["1", "b2", "2", "b3", "3", "4", "#4", "5", "#5", "6", "b7", "7"],
          "augmented": ["1", "#2", "3", "5", "#5", "7"],
          "enigmatic ascending": ["1", "b2", "3", "#4", "#5", "#6", "7"],
          "enigmatic descending": ["1", "b2", "3", "4", "b6", "b7", "7"],
          "hungarian major": ["1", "b3", "3", "b5", "5", "6", "b7"],
          "neapolitan major": ["1", "b2", "b3", "4", "5", "6", "7"],
          "neapolitan minor": ["1", "b2", "b3", "4", "5", "b6", "7"],
          "prometheus": ["1", "2", "3", "b5", "6", "b7"],
          "mystic": ["1", "2", "3", "b5", "6", "b7"],
          "prometheus neapolitan": ["1", "b2", "3", "b5", "6", "b7"], # Prometheus with lowered 2
          "spanish 8 tone": ["1", "b2", "b3", "3", "4", "b5", "b6", "b7"],
          }

# Invert scales so alternative names can be identified by intervals or name
d = defaultdict(list)
[d[tuple(v)].append(k) for k,v in SCALES.items()]
INV_SCALES_BY_INTERVAL = dict(d)
INV_SCALES_BY_NAME = {k: d[tuple(v)] for k,v in SCALES.items()}

In [ ]:
#|hide
for item in [BASE_NOTES, CHROMATIC_NOTES, INTERVALS]:
    assert len(item) == len(set(item)), f"Duplicate {item} found in {item}"
assert len(CHROMATIC_NOTES) == 12
assert len(INTERVALS) == 12
assert len(SCALES) == len(INV_SCALES_BY_NAME)

# Note

The `Note` is the basic atomic unit in music. Combinations of notes will form chords and scales. Notes and chords form songs.

In [ ]:
#|export
class Note(BasicRepr):
    def __init__(self, note: str, oct: int = 4):
        assert isinstance(oct, int) and oct > 0, f"Octave must be a positive integer, got oct={oct}."
        store_attr()
        # Transform note to uppercase
        if isinstance(note, str):
            note = note[0].upper() + note[1:]
            assert mingus_notes.is_valid_note(note), f"Note '{note}' is not valid"
            self.note = self.postprocess_note(mingus_notes.remove_redundant_accidentals(note))

    @staticmethod
    def postprocess_note(note: str):
        """ Get rid of unnecessary accidentals."""
        if note == "B#": note = "C"
        elif note == "E#": note = "F"
        elif note == "Cb": note = "B"
        elif note == "Fb": note = "E"
        elif note.endswith("##"):
            note = BASE_NOTES[BASE_NOTES.index(note[0])+1]
        elif note.endswith("bb"):
            note = BASE_NOTES[BASE_NOTES.index(note[0])-1]
        return str(note)
    
    def __str__(self): return self.note
    def __int__(self): return NOTE_MAPPING[str(self)]
    def rel(self): return self.oct * 12 + int(self)
    def __eq__(self, other): return self.rel() == other.rel()
    def __ne__(self, other): return self.rel() != other.rel()
    def __lt__(self, other): return self.rel() < other.rel()
    def __le__(self, other): return self.rel() <= other.rel()
    def __gt__(self, other): return self.rel() > other.rel()
    def __ge__(self, other): return self.rel() >= other.rel()

Every note has an accompanying octave `oct` associated with it. This is useful later for determining intervals and playing the sound of the notes.

In [ ]:
a_sharp = Note("A#")
a_sharp

Note(note='A#', oct=4)

Each note has an integer value which shows its place in a C octave (`C == 0`, `C# == 1`, `B == 11`, etc.)

In this example `A#` should denote `10` as its integer value.

In [ ]:
assert int(a_sharp) == 10
int(a_sharp)

10

In [ ]:
assert str(a_sharp) == "A#"
a_sharp.note

'A#'

In [ ]:
c_sharp = Note("C#")
c_sharp

Note(note='C#', oct=4)

Notes can be compared with each other using familiar Python operators. Here are some examples of comparison between `Note` objects.

In [ ]:
assert Note("E#") == Note("F")
assert Note("B#") == Note("C")
assert Note("C##") == Note("D")
assert Note("Fb") == Note("E")
assert Note("Abb") == Note("G")
assert Note("Bbb") == Note("A")
assert Note("Cb") == Note("B")
assert Note("C") == Note("C")
assert Note("E#") == Note("F")
assert Note("A#") != Note("B")
assert Note("F") > Note("C#")
assert Note("B#") <= Note("C")
assert Note("C") < Note("B")
assert Note("E") >= Note("E")
assert Note("C", oct=4) > Note("B", oct=3)
assert Note("C", oct=4) != Note("C", oct=5)
assert Note("C", oct=4) < Note("C", oct=5)

## Adding to Note

Adding semitones to a note will return a new note with `n` semitones added above the original note.

For example, adding 1 semitone to `A#` (A Sharp) will return `B`.

Adding `Note` objects together will form a `Chord`. More on that in the `Chord` section.

In [ ]:
#|export
@patch
def __add__(self:Note, other):
    """Add n semitones to a note."""
    octave_change = (other + int(self)) // 12
    return Note(CHROMATIC_NOTES[(int(self) + other) % 12], oct=self.oct + octave_change)

@patch
def __mod__(self:Note, other):
    """Add n whole notes."""
    return self + other * 2

In [ ]:
for i in range(1, 13):
    print(a_sharp+i)

B
C
C#
D
D#
E
F
F#
G
G#
A
A#


The octave of the note is automatically updated when adding.

In [ ]:
assert (a_sharp+1).oct == a_sharp.oct
assert (a_sharp+2).oct == a_sharp.oct + 1
assert (Note("C")+11).oct == Note("C").oct

In [ ]:
assert Note("C")+11 == Note("B")
assert str(a_sharp+1) == "B"
assert str(a_sharp+11) == "A"
assert str(a_sharp+12) == "A#"
assert str(a_sharp+13) == "B"
assert str(a_sharp+47) == "A"
assert str(a_sharp+0) == "A#"

The `%` operator is a shortcut for adding whole notes.

In [ ]:
assert a_sharp % 1 == Note("C", oct=5)
a_sharp % 1

Note(note='C', oct=5)

In [ ]:
for i in range(1, 7):
    print(a_sharp % i)

C
D
E
F#
G#
A#


In [ ]:
assert str(a_sharp % 1) == "C"
assert str(a_sharp % 0) == "A#"
assert str(a_sharp % 6) == "A#"
assert str(a_sharp % 6 + 1) == "B"

## Subtracting from Note

Subtracting semitones from a `Note` returns a new note with `n` semitones subtracted from the original note.

For example, subtracting 1 semitone from `C` returns `B`. Subtracting 1 semitone from `A#` returns `A`.


In [ ]:
#|export
@patch
def __sub__(self:Note, other):
    """Subtract n semitones from a note."""
    octave_change = (other + int(self)) // 12
    return Note(CHROMATIC_NOTES[(int(self) - other) % 12], oct=self.oct - octave_change)

@patch
def __floordiv__(self:Note, other):
    """Subtract n whole notes"""
    return self - other * 2

In [ ]:
for i in range(1, 13):
    print(a_sharp-i)

A
G#
G
F#
F
E
D#
D
C#
C
B
A#


In [ ]:
assert (a_sharp-1).oct == a_sharp.oct
assert (a_sharp-10).oct == a_sharp.oct - 1
assert (a_sharp-6).oct == a_sharp.oct - 1
assert (a_sharp-12).oct == a_sharp.oct - 1

In [ ]:
assert str(a_sharp-0) == "A#"
assert str(a_sharp-1) == "A"
assert str(a_sharp-11) == "B"
assert str(a_sharp-12) == "A#"
assert str(a_sharp-13) == "A"
assert str(a_sharp-25) == "A"

The `//` operator is a shortcut for subtracting whole notes.

In [ ]:
assert a_sharp // 1 == Note("G#", oct=3)
a_sharp // 1

Note(note='G#', oct=3)

In [ ]:
for i in range(1, 7):
    print(a_sharp // i)

G#
F#
E
D
C
A#


In [ ]:
assert str(a_sharp // 1) == "G#"
assert str(a_sharp // 0) == "A#"
assert str(a_sharp // 6) == "A#"
assert str(a_sharp // 6 + 1) == "B"

## Interval

Two notes can be combined to form an interval. `interval` returns an `Interval` object from which you can get the long or short name.

In [ ]:
#|export 
class Interval:
    def __init__(self, note1: Note, note2: Note):
        store_attr()
        self.notes = [note1, note2]
        self.semitones = self.set_semitones()
    
    @property
    def short(self): return STEPS_TO_INTERVAL[abs(self.semitones)]
    @property
    def long(self): return STEPS_TO_INTERVAL_FULL[abs(self.semitones)]

    def set_semitones(self):
        # TODO Add upper extensions to semitone calculation and interval names (2+ octaves)
        return (12 + int(self.note2) - int(self.note1) + (self.note2.oct - self.note1.oct) * 12) % 12

    def __repr__(self): return f"{str(self.long)} ({str(self.short)})"
    def __eq__(self, other): return self.semitones == other.semitones
    def __ne__(self, other): return not self.semitones == other.semitones
    def __lt__(self, other): return self.semitones < other.semitones
    def __le__(self, other): return self.semitones <= other.semitones
    def __gt__(self, other): return self.semitones > other.semitones
    def __ge__(self, other): return self.semitones >= other.semitones
    def __abs__(self): 
        c = Interval(self.note1, self.note2)
        c.semitones = abs(c.semitones)
        return c

Calling `interval` on a `Note` object requires providing another `Note` object and returns an `Interval` object. A shortcut is to use the `&` operator and has the same effect.

In [ ]:
#|export
@patch
def interval(self:Note, other:Note): return Interval(self, other)

@patch
def __and__(self:Note, other:Note): return self.interval(other)

The full name of the interval between `A#` and `C#` is a `minor third`.

In [ ]:
c_sharp = Note("C#")
m3 = a_sharp.interval(c_sharp)
m3

minor third (b3)

From here on in these docs we'll use the more compact `&` syntax, but feel free to use what works best for you.

In [ ]:
assert m3 == a_sharp & c_sharp
a_sharp & c_sharp

minor third (b3)

In [ ]:
assert (Note("C", oct=5) & Note("D", oct=5)).semitones == 2
assert (Note("C", oct=2) & Note("E", oct=2)).short == "3"
assert (Note("C", oct=5) & Note("A", oct=5)).long == "major sixth"
assert (Note("C", oct=5) & Note("B", oct=5)).long == "major seventh"
assert (Note("C", oct=5) & Note("D", oct=5)).long == "major second"
assert (Note("C", oct=5) & Note("C", oct=6)).long == "unison"
assert (Note("C", oct=5) & Note("C", oct=7)).long == "unison"
assert (Note("C", oct=5) & Note("D", oct=6)).notes == [Note("C", oct=5), Note("D", oct=6)]
assert (Note("C", oct=5) & Note("D", oct=5)).notes == [Note("C", oct=5), Note("D", oct=5)]

A minor third is 3 semitones apart.

In [ ]:
assert m3.semitones == 3
m3.semitones

3

The shorthand for a `minor third` interval is `b3`.

In [ ]:
assert m3.long == "minor third"
m3.long

'minor third'

In [ ]:
assert m3.short == "b3"
m3.short

'b3'

In [ ]:
ninth = Note("G#", oct=5) & Note("A", oct=6)
assert ninth.semitones == 1
ninth

minor second (b2)

`Interval` objects can be compared with each other. For a single octave the minor 3rd as larger than the ninth (i.e. minor 2nd).

In [ ]:
assert m3 >= ninth
assert m3 != ninth
assert not m3 < ninth

Note that with negative intervals its a different story. `C#` compared with `A#` is a major 6th.

In [ ]:
low_a_sharp = Note("A#", oct=3)
neg_m3 = c_sharp & low_a_sharp
neg_m3

major sixth (6)

In [ ]:
assert neg_m3 > m3
assert neg_m3 != m3

An `Interval` can also determine its type. An interval can be:

- `Perfect consonant` (Unison, Octave and 5th)
- `Soft consonant` (3rds and 6ths), 
- `Mild Dissonant` (Minor 7th and Major 2nd), 
- `Sharp Dissonant` (Major 7th and Minor 2nd), 
- `Contextual` (4th)
- `Neutral` (Tritone).

In [ ]:
#|export
@patch
def type(self:Interval): return INTERVAL_TYPES[abs(self.semitones) % 12]

A fifth is a `Perfect Consonant`.

In [ ]:
fifth = Note("C") & Note("G")
assert fifth.type() == "Perfect Consonant"
fifth.type()

'Perfect Consonant'

A minor second is `Sharp Dissonant`.

In [ ]:
m2 = Note("C") & Note("C#")
assert m2.type() == "Sharp Dissonant"
m2.type()

'Sharp Dissonant'

A special case is the fourth which is `Contextual`. This can be soft consonant or dissonant depending on the context of harmonic movement and is not feasible to determine within one interval.

In [ ]:
fourth = Note("C") & Note("F")
assert fourth.type() == "Contextual"
fourth.type()

'Contextual'

The `Interval.type` method handles upper extensions by comparing it within the same octave. For example a flat 9 (`b9`) is treated as a minor second and therefore `Sharp Dissonant`.

In [ ]:
ninth = Note("B", oct=4) & Note("C", oct=5)
ninth.type()

'Sharp Dissonant'

You can add to `Interval` objects to augment or diminish it.

In [ ]:
#|export
@patch
def __add__(self:Interval, other):
    return Interval(self.note1, self.note2+other)

@patch 
def __sub__(self:Interval, other):
    return Interval(self.note1, self.note2-other)

In this example, we augment a minor 3rd interval to a major 3rd (`b3`->`3`)

In [ ]:
m3 = a_sharp & c_sharp
m3

minor third (b3)

In [ ]:
assert (m3 + 1).long == "major third"
m3 + 1

major third (3)

If we diminish the minor 3rd interval it becomes a major 2nd (`b3`->`2`).

In [ ]:
assert (m3 - 1).long == "major second"
m3 - 1

major second (2)

## Convert to Major or Minor

`Note` objects can be converted to its relative major or minor. How this is converted is visualized on the circle of fifths.

<img src="https://upload.wikimedia.org/wikipedia/commons/3/33/Circle_of_fifths_deluxe_4.svg" width="40%" alt="Circle of Fifths">

For example, the relative minor of C is A. The relative major of C# is E.

`minor` converts an arbitrary note to its relative minor. This means 3 semitones are subtracted from the note.

In [ ]:
#|export
@patch
def minor(self:Note): return self - 3

In [ ]:
c = Note("C")
assert str(c.minor()) == "A"
c.minor()

Note(note='A', oct=4)

`major` converts an arbitrary note to its relative major. This means 3 semitones are added to the note.

In [ ]:
#|export
@patch
def major(self:Note): return self + 3

In [ ]:
assert str(c_sharp.major()) == "E"
c_sharp.major()

Note(note='E', oct=4)

## Play Audio

Every `Note` can be played as audio. A `Note` is first transformed into a bytestring.

In [ ]:
#|export
@patch 
def get_audio_array(self:Note, length=1, sr=44100):
    a = {'C':0,'C#':1,'Db':1,'D':2,'D#':3,'Eb':3,'E':4,'F':5,
         'F#':6,'Gb':6,'G':7,'G#':8,'Ab':8,'A':9,'A#':10,'Bb':10,'B':11}
    t = np.linspace(0, length, int(sr * length), False)
    def freq(n): return 440 * 2**((12 * (int(n[-1])+1) + a[n[:-1]] - 69)/12)
    wave = np.sin(2 * np.pi * freq(f"{self.note}{self.oct}") * t)
    wave = (wave / np.max(np.abs(wave)) * 32767).astype(np.int16)
    return wave

@patch
def get_audio_bytes(self:Note, length=1, sr=44100):
    buf = io.BytesIO(); wav.write(buf, sr, self.get_audio_array(length, sr))
    return buf.getvalue()

In [ ]:
c.get_audio_bytes(length=5)[:50]

b'RIFF\xcc\xba\x06\x00WAVEfmt \x10\x00\x00\x00\x01\x00\x01\x00D\xac\x00\x00\x88X\x01\x00\x02\x00\x10\x00data\xa8\xba\x06\x00\x00\x00\xc5\x04\x88\t'

For convenience, we can also play the audio directly.

In [ ]:
#|export
@patch
def play(self:Note, length=1): return Audio(data=self.get_audio_bytes(length))

In [ ]:
c.play()

THe length of a specific note can be specified for the audio.

In [ ]:
c.play(length=2)

In [ ]:
a_sharp.play()

Also here, method chaining is possible.

In [ ]:
(a_sharp - 6).play()

# Chord

The `Chord` class is a collection of notes played together. The name of the chord is automatically inferred from the notes.

In [ ]:
#|export
class Chord(BasicRepr):
    def __init__(self, notes: List[Note]):
        self.notes = [Note(n) if isinstance(n, str) else n for n in notes]
        self.s_notes = [str(n) for n in self.notes]
        self.short_s_notes = [f"{n.note}{n.oct}" for n in self.notes]
        self.first = self.notes[0]
        self.s_first = str(self.first)

    def names(self) -> list[str]: return mingus_chords.determine(self.s_notes)
    def name(self): return self.names()[0] if self.names() else "No chord found."

    @classmethod
    def from_short(cls, c: str): return cls(mingus_chords.from_shorthand(c)) 

    def __repr__(self): return f"Chord: '{self.name()}'. Notes: {self.short_s_notes}"
    def __add__(self, other): return Chord([n + other for n in self.notes])
    def __sub__(self, other): return Chord([n - other for n in self.notes])
    def __mod__(self, other): return Chord([n % other for n in self.notes])
    def __floordiv__(self, other): return Chord([n // other for n in self.notes])
    def __iter__(self) -> list[str]: return iter(self.notes)
    
    def _compare_notes(self, other, op): return all(op(n1, n2) for n1, n2 in zip(self.notes, other.notes))
    def __eq__(self, other): return self.first == other.first and self._compare_notes(other, lambda x, y: x == y)
    def __ne__(self, other): return not self == other
    def __lt__(self, other): return self.first < other.first or (self.first == other.first and self._compare_notes(other, lambda x, y: x < y))
    def __le__(self, other): return self.first < other.first or (self.first == other.first and self._compare_notes(other, lambda x, y: x <= y))
    def __gt__(self, other): return self.first > other.first or (self.first == other.first and self._compare_notes(other, lambda x, y: x > y))
    def __ge__(self, other): return self.first > other.first or (self.first == other.first and self._compare_notes(other, lambda x, y: x >= y))


class PolyChord(Chord):
    def __init__(self, chords: list[Chord]):
        self.chords = chords
        super().__init__([note for chord in chords for note in chord.notes])
    def __repr__(self): return f"PolyChord: '{'|'.join([c.name() for c in self.chords])}'. Notes: {self.short_s_notes}"

In [ ]:
c_major = Chord(["C", "E", "G"])
c_major

Chord: 'C major triad'. Notes: ['C4', 'E4', 'G4']

`Chord` objects can be created from a string.

In [ ]:
cmaj7 = Chord.from_short("Cmaj7")
cmaj7

Chord: 'C major seventh'. Notes: ['C4', 'E4', 'G4', 'B4']

`Chord` objects can be compared to each other using familiar Python operators. The length of the chords and the underlying notes are compared. For example, A C major chord is technically lower than a C major 7th chord. The 1st 3 notes are the same, but Cmaj7 has an additional 4th note.

In [ ]:
assert c_major <= cmaj7

Length is only a tie breaker. For example an E major chord clearly higher than a D major 7 chord, because its root note is higher.

In [ ]:
assert Chord.from_short("E") >= Chord.from_short("Dmaj7")

`Chord` objects can be transposed in the same way as `Note` objects.

In [ ]:
cmaj7 + 2

Chord: 'D major seventh'. Notes: ['D4', 'F#4', 'A4', 'C#5']

In [ ]:
# Dmaj7 > Cmaj7
cmaj7 + 2 > cmaj7

True

As with `Note` objects, there are shortcuts for transposing whole notes up and down by using the `%` and `//` operators, respectively.

In [ ]:
assert cmaj7 + 2 == cmaj7 % 1
# Transpose up 1 whole note
cmaj7 % 1

Chord: 'D major seventh'. Notes: ['D4', 'F#4', 'A4', 'C#5']

In [ ]:
# Transpose down 5 whole notes (Same Dmaj7 chord but 1 octave lower)
cmaj7 // 5

Chord: 'D major seventh'. Notes: ['D4', 'F#3', 'A3', 'C#3']

`Chord` objects can be created by multiplying `Note` objects. `Chord` objects can be augmented by multiplying them with `Note` objects.

In [ ]:
#|export
@patch
def __mul__(self:Note, other: Note):
    return Chord([self, other])

@patch
def __mul__(self:Chord, other):
    if isinstance(other, Note):
        return Chord(self.notes + [other])
    elif isinstance(other, Chord):
        return PolyChord([self, other])
    else:
        raise ValueError("Chord objects can only be multiplied with Note or other Chord objects")

In [ ]:
# Eb/C slash chord
eb_over_c = Note("Eb", oct=3) * Note("C", oct=4) * Note("E", oct=4) * Note("G", oct=4)
eb_over_c

Chord: 'No chord found.'. Notes: ['Eb3', 'C4', 'E4', 'G4']

For more advanced use cases, `Chord` objects can multiplied into a `PolyChord`.

In [ ]:
poly_chord = cmaj7 * Chord(Note(n, oct=5) for n in ["A", "D", "E"])
poly_chord

PolyChord: 'C major seventh|A suspended fourth triad'. Notes: ['C4', 'E4', 'G4', 'B4', 'A5', 'D5', 'E5']

`Chord` and `PolyChord` objects can be inverted with `invert`.

In [ ]:
#|export
@patch
def invert(self:Chord, n: int = 1):
    assert n > 0 and n < len(self.s_notes), f"Invalid inversion '{n}' for chord with '{len(self.s_notes)}' notes."
    return Chord(self.notes[n:] + [Note(str(note), oct=note.oct + 1) for note in self.notes[:n]])

@patch
def invert(self:PolyChord, n: int = 1):
    return PolyChord([c.invert(n) for c in self.chords])

In [ ]:
cmaj7.invert(2)

Chord: 'C major seventh, second inversion'. Notes: ['G4', 'B4', 'C5', 'E5']

In [ ]:
poly_chord.invert(1)

PolyChord: 'C major seventh, first inversion|D suspended second triad'. Notes: ['E4', 'G4', 'B4', 'C5', 'D5', 'E5', 'A6']

`Interval` objects can be obtained for a `Chord`.

In [ ]:
#|export
@patch
def intervals(self:Chord):
    return [Interval(n1, n2) for n1, n2 in zip(self.notes, self.notes[1:])]

In [ ]:
cmaj7_intervals = cmaj7.intervals()
assert len(cmaj7_intervals) == 3
assert cmaj7_intervals[0].short == "3"

In [ ]:
cmaj7_intervals

[major third (3), minor third (b3), major third (3)]

In [ ]:
poly_chord.intervals()

[major third (3),
 minor third (b3),
 major third (3),
 minor seventh (b7),
 perfect fourth (4),
 major second (2)]

`Chord` and `PolyChord` objects can be played, just like `Note` objects.

In [ ]:
#|export
@patch
def get_audio_array(self:Chord, length=1):
    return np.sum([n.get_audio_array(length) for n in self.notes], axis=0)

@patch
def play(self:Chord, length=1): 
    return Audio(self.get_audio_array(length), rate=44100)

In [ ]:
cmaj7.play()

In [ ]:
cmaj7.invert(1).play()

In [ ]:
eb_over_c.play()

In [ ]:
Chord.from_short("Dbdim7").play()

In [ ]:
poly_chord.play()

TODO: Check which scales/modes the chord belongs to.

# Scale

The basic scale is a collection of intervals and agnostic to any key. From the basic scale, notes can be derived by providing a root note.

In [ ]:
#|export
class Scale:
    def __init__(self, name: str):
        self.name = name.lower()
        self.intervals = SCALES.get(self.name, "scale not found.")

    @classmethod
    def available_scales(cls): return list(SCALES.keys())
    
    @classmethod
    def from_intervals(cls, name: str, intervals: list[str]):
        """Create a custom scale from a list of intervals."""
        for i in intervals:
            assert i in list(INTERVAL_NAMES), f"Interval '{i}' not valid. Available intervals: '{list(INTERVAL_NAMES.keys())}'"
        custom_scale = cls(name)
        custom_scale.intervals = intervals
        return custom_scale
    
    @property
    def rel_semitones(self):
        return [INTERVAL_HALF_STEPS[interval] for interval in self.intervals]
    
    @property
    def abs_semitones(self):
        rel = self.rel_semitones
        abs = []
        for i, r in enumerate(rel[1:]):
            abs.append(r - rel[i])
        # Last remaining interval
        abs.append(12-sum(abs))
        return abs
    
    @property
    def interval_names(self):
        return [INTERVAL_NAMES[i] for i in self.intervals[1:]]
    
    def __repr__(self): return f"Scale: {self.name.title()}. Intervals: {self.intervals}"
    def __eq__(self, other): return self.intervals == other.intervals
    def __ne__(self, other): return not self == other
    def __iter__(self) -> list[str]: return iter(self.intervals)

The basic `Scale` representation gives you the name and intervals of the scale.

In [ ]:
major = Scale("major")
major

Scale: Major. Intervals: ['1', '2', '3', '4', '5', '6', '7']

Listify the scale to get the intervals or call `.intervals`.

In [ ]:
dorian = Scale("dorian")
dorian

Scale: Dorian. Intervals: ['1', '2', 'b3', '4', '5', '6', 'b7']

In [ ]:
lydian = Scale("lydian")
lydian

Scale: Lydian. Intervals: ['1', '2', '3', '#4', '5', '6', '7']

Semitones for the invervals in a scale can be retrieved in an absolute (intervals between notes) or relative (intervals from root).

In [ ]:
assert major.rel_semitones == [0, 2, 4, 5, 7, 9, 11]
major.rel_semitones

[0, 2, 4, 5, 7, 9, 11]

In [ ]:
assert major.abs_semitones == [2, 2, 1, 2, 2, 2, 1]
assert sum(major.abs_semitones) == 12
major.abs_semitones

[2, 2, 1, 2, 2, 2, 1]

Scales can be compared to each other.

In [ ]:
list(Scale("minor")), list(Scale("aeolian"))

(['1', '2', 'b3', '4', '5', 'b6', 'b7'],
 ['1', '2', 'b3', '4', '5', 'b6', 'b7'])

In [ ]:
assert not major == dorian
assert lydian != dorian
assert lydian == lydian
assert Scale("minor") == Scale("aeolian")

Many of the scales are available, but custom scales can be created with `from_intervals`. Consult `Scale.available_scales` to get the built-in scales.

Here we create a custom Persian scale.

In [ ]:
persian = Scale.from_intervals("persian", ["1", "b2", "3", "4", "b5", "b6", "7"])
persian

Scale: Persian. Intervals: ['1', 'b2', '3', '4', 'b5', 'b6', '7']

In [ ]:
#|export
@patch
def get_notes(self:Scale, root, oct=4):
    """Get the notes of a scale from a root note."""
    root = Note(root, oct=oct) if isinstance(root, str) else root
    return [root + int(INTERVAL_HALF_STEPS[i]) for i in self.intervals]

In [ ]:
c_major = Scale("major").get_notes("C")
assert [str(n) for n in c_major] == ['C', 'D', 'E', 'F', 'G', 'A', 'B']
c_major

[Note(note='C', oct=4),
 Note(note='D', oct=4),
 Note(note='E', oct=4),
 Note(note='F', oct=4),
 Note(note='G', oct=4),
 Note(note='A', oct=4),
 Note(note='B', oct=4)]

In [ ]:
g_major = Scale("major").get_notes("G")
g_major

[Note(note='G', oct=4),
 Note(note='A', oct=4),
 Note(note='B', oct=4),
 Note(note='C', oct=5),
 Note(note='D', oct=5),
 Note(note='E', oct=5),
 Note(note='F#', oct=5)]

In [ ]:
c_dorian = Scale("dorian").get_notes("C")
assert [str(n) for n in c_dorian] == ['C', 'D', 'D#', 'F', 'G', 'A', 'A#']
c_dorian

[Note(note='C', oct=4),
 Note(note='D', oct=4),
 Note(note='D#', oct=4),
 Note(note='F', oct=4),
 Note(note='G', oct=4),
 Note(note='A', oct=4),
 Note(note='A#', oct=4)]

If needed you can get all diatonic chords in the scale. 

In [ ]:
#|export
@patch
def get_diatonic_chords(self:Scale, root, min_notes=3):
    assert min_notes > 1, "min_notes must be greater than 1."
    notes = self.get_notes(root)
    return [Chord(combo) for n in range(min_notes, len(notes)+1) for combo in combinations(notes, n)]

For example, let's look at all the diatonic E chords in the C major scale we can identify.

In [ ]:
[c for c in Scale("major").get_diatonic_chords("C") if "E" in c.name()]

[Chord: 'E minor seventh, second inversion'. Notes: ['D4', 'E4', 'G4'],
 Chord: 'E minor seventh, second inversion'. Notes: ['D4', 'E4', 'B4'],
 Chord: 'E minor triad'. Notes: ['E4', 'G4', 'B4'],
 Chord: 'E suspended fourth triad'. Notes: ['E4', 'A4', 'B4'],
 Chord: 'Esus4|CM6'. Notes: ['C4', 'E4', 'A4', 'B4'],
 Chord: 'E suspended seventh, third inversion'. Notes: ['D4', 'E4', 'A4', 'B4']]

`get_interval_names` shows all interval names of a scale.

In [ ]:
#|export
@patch
def get_interval_names(self:Scale, short=False):
    return self.intervals if short else self.interval_names

In [ ]:
major.get_interval_names()

['major second',
 'major third',
 'perfect fourth',
 'perfect fifth',
 'major sixth',
 'major seventh']

In [ ]:
major.get_interval_names(short=True)

['1', '2', '3', '4', '5', '6', '7']

In [ ]:
persian.get_interval_names()

['minor second',
 'major third',
 'perfect fourth',
 'diminished fifth',
 'minor sixth',
 'major seventh']

Many scales often have alternative names. We can derive them using `get_scale_names`.

In [ ]:
#|export
@patch
def get_scale_names(self:Scale):
    return INV_SCALES_BY_INTERVAL.get(tuple(self.intervals), [])

In [ ]:
assert major.get_scale_names() == ["ionian", "major"]
major.get_scale_names()

['ionian', 'major']

In [ ]:
wild_custom = Scale.from_intervals(name="wild custom", intervals=["1", "b2", "2", "b3", "b5",
                                                                   "5", "b6", "b7", "7"])
assert not wild_custom.get_scale_names()
wild_custom.get_scale_names()

[]

A derived scale can be played in a given key.

In [ ]:
major.get_notes("C")

[Note(note='C', oct=4),
 Note(note='D', oct=4),
 Note(note='E', oct=4),
 Note(note='F', oct=4),
 Note(note='G', oct=4),
 Note(note='A', oct=4),
 Note(note='B', oct=4)]

In [ ]:
#|export
@patch
def get_audio_array(self:Scale, root, oct=4, length=0.3):
    notes = self.get_notes(root, oct=oct)
    octave = Note(root, oct=oct+1).get_audio_array(length=length)
    return np.concatenate([n.get_audio_array(length) for n in notes] + [octave])

@patch
def play(self:Scale, root, oct=4, length=0.3): 
    return Audio(self.get_audio_array(root, oct=oct, length=length), rate=44100)

In [ ]:
major.play("C")

In [ ]:
persian.play("C")

In [ ]:
wild_custom.play("C")

In [ ]:
Scale("altered").play("C", length=0.2, oct=3)

In [ ]:
Scale("aeolian dominant").play("C", length=0.2, oct=3)

We can derive all triads in the `Scale`.

In [ ]:
#|export
@patch
def get_triads(self:Scale, root):
    """Get all triads in scale starting from root note."""
    notes = self.get_notes(root)
    return [Chord([notes[i], 
                  Note(str(notes[(i+2)%7]), oct=notes[i].oct + (i+2)//7),
                  Note(str(notes[(i+4)%7]), oct=notes[i].oct + (i+4)//7)]) 
            for i in range(len(notes))]

In [ ]:
c_major_triads = major.get_triads("C")
c_major_triads

[Chord: 'C major triad'. Notes: ['C4', 'E4', 'G4'],
 Chord: 'D minor triad'. Notes: ['D4', 'F4', 'A4'],
 Chord: 'E minor triad'. Notes: ['E4', 'G4', 'B4'],
 Chord: 'F major triad'. Notes: ['F4', 'A4', 'C5'],
 Chord: 'G major triad'. Notes: ['G4', 'B4', 'D5'],
 Chord: 'A minor triad'. Notes: ['A4', 'C5', 'E5'],
 Chord: 'B diminished triad'. Notes: ['B4', 'D5', 'F5']]

In [ ]:
#|export
@patch
def play_triads(self:Scale, root):
    """Play all triads in scale starting from root note."""
    return Audio(np.concatenate([c.get_audio_array() for c in self.get_triads(root)]), rate=44100)

All triads in a given `Scale` can be played.

In [ ]:
major.play_triads("C")

In [ ]:
Scale("phrygian").get_triads("D")

[Chord: 'D minor triad'. Notes: ['D4', 'F4', 'A4'],
 Chord: 'No chord found.'. Notes: ['D#4', 'G4', 'A#4'],
 Chord: 'F major triad'. Notes: ['F4', 'A4', 'C4'],
 Chord: 'No chord found.'. Notes: ['G4', 'A#4', 'D5'],
 Chord: 'No chord found.'. Notes: ['A4', 'C4', 'D#5'],
 Chord: 'No chord found.'. Notes: ['A#4', 'D5', 'F5'],
 Chord: 'No chord found.'. Notes: ['C5', 'D#6', 'G6']]

We can also get all seventh chords in the `Scale`.

In [ ]:
#|export
@patch
def get_sevenths(self:Scale, root):
    """Get all seventh chords in scale starting from root note."""
    notes = self.get_notes(root)
    return [Chord([notes[i], 
                  Note(str(notes[(i+2)%7]), oct=notes[i].oct + (i+2)//7),
                  Note(str(notes[(i+4)%7]), oct=notes[i].oct + (i+4)//7),
                  Note(str(notes[(i+6)%7]), oct=notes[i].oct + (i+6)//7)]) 
            for i in range(len(notes))]

In [ ]:
c_seventh_triads = major.get_sevenths("C")
c_seventh_triads

[Chord: 'C major seventh'. Notes: ['C4', 'E4', 'G4', 'B4'],
 Chord: 'D minor seventh'. Notes: ['D4', 'F4', 'A4', 'C5'],
 Chord: 'E minor seventh'. Notes: ['E4', 'G4', 'B4', 'D5'],
 Chord: 'F major seventh'. Notes: ['F4', 'A4', 'C5', 'E5'],
 Chord: 'G dominant seventh'. Notes: ['G4', 'B4', 'D5', 'F5'],
 Chord: 'A minor seventh'. Notes: ['A4', 'C5', 'E5', 'G5'],
 Chord: 'B half diminished seventh'. Notes: ['B4', 'D5', 'F5', 'A5']]

And play them.

In [ ]:
#|export
@patch
def play_sevenths(self:Scale, root):
    """Play all seventh chords in scale starting from root note."""
    return Audio(np.concatenate([c.get_audio_array() for c in self.get_sevenths(root)]), rate=44100)

In [ ]:
major.play_sevenths("C")

In [ ]:
lydian.get_sevenths("D")

[Chord: 'D major seventh'. Notes: ['D4', 'F#4', 'A4', 'C#4'],
 Chord: 'E dominant seventh'. Notes: ['E4', 'G#4', 'B4', 'D5'],
 Chord: 'F# minor seventh'. Notes: ['F#4', 'A4', 'C#4', 'E5'],
 Chord: 'G# half diminished seventh'. Notes: ['G#4', 'B4', 'D5', 'F#5'],
 Chord: 'A major seventh'. Notes: ['A4', 'C#4', 'E5', 'G#5'],
 Chord: 'B minor seventh'. Notes: ['B4', 'D5', 'F#5', 'A5'],
 Chord: 'C# minor seventh'. Notes: ['C#5', 'E6', 'G#6', 'B6']]

We can display all relevant information from the scale in a Pandas DataFrame table.

In [ ]:
#|export
@patch
def to_frame(self:Scale, root=None):
    d = {
        "Intervals": self.intervals,
        "Relative Semitones": self.rel_semitones,
        "Absolute Semitones": self.abs_semitones,
    }
    if root:
        d.update({
            "Notes": self.get_notes(root),
            "Triads": [t.name() for t in self.get_triads(root)],
            "Seventh Chords": [s.name() for s in self.get_sevenths(root)],
        })
    return pd.DataFrame(d)

The `to_frame` method can called without a root note, but is most informative when given a root note. In that case also the triads and seventh chords are displayed.

In [ ]:
major.to_frame(root="D")

Intervals  Relative Semitones  Absolute Semitones Notes  \
0         1                   0                   2     D   
1         2                   2                   2     E   
2         3                   4                   1    F#   
3         4                   5                   2     G   
4         5                   7                   2     A   
5         6                   9                   2     B   
6         7                  11                   1    C#   

                Triads              Seventh Chords  
0        D major triad             D major seventh  
1        E minor triad             E minor seventh  
2       F# minor triad            F# minor seventh  
3        G major triad             G major seventh  
4        A major triad          A dominant seventh  
5        B minor triad             B minor seventh  
6  C# diminished triad  C# half diminished seventh

TODO: Comparison method for scales

TODO: Get all modes of a scale

FIX: Identify all diatonic chords in a scale.

TODO: Check if chord is diatonic within a scale.

In [ ]:
#| hide
import nbdev; nbdev.nbdev_export()